In [1]:

import pandas as pd
import numpy as np
import xarray as xr
from ecephys import wne, utils, sglxr
import wisc_ecephys_tools as wet
import thefuzz
from ecephys.wne.sglx.utils import get_sglx_file_counterparts


/home/tbugnon/projects/ecephys_dev/ephyviewer/ephyviewer/datasource/neosource.py:16: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if V(neo.__version__) >= "0.6.0":
/home/tbugnon/miniconda3/envs/ecephys_dev/lib/python3.10/site-packages/setuptools/_distutils/version.py:346: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  other = LooseVersion(other)
/home/tbugnon/projects/ecephys_dev/ephyviewer/ephyviewer/datasource/spikeinterfacesources.py:10: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  if V(spikeinterface.__version__) >= "0.90.1":
/home/tbugnon/miniconda3/envs/ecephys_dev/lib/python3.10/site-packages/setuptools/_distutils/version.py:346: DeprecationWarning: distutils Version classes are deprecated. Use packaging.version instead.
  other = LooseVersion(other)


In [2]:
anatomyProjectName = "shared_s3"
lfpProjectName = "seahorse"

experiment = "novel_objects_deprivation"
alias = "full"

In [3]:
wneAnatomyProject = wet.get_wne_project("shared_s3")

# Use acronyms from Waxholm atlas!

In [31]:
from bg_atlasapi.bg_atlas import BrainGlobeAtlas
atlas = BrainGlobeAtlas("whs_sd_rat_39um", brainglobe_dir="/Volumes/npx_nfs/shared_s3/.brainglobe")

pd.set_option('display.max_rows', None)
atlas_df = atlas.lookup_df.set_index("acronym")
atlas_df

id                                               name
acronym                                                                 
root            10000                                               Root
Brain            1000                                              Brain
wmt              1001                                       White matter
olf              1050                             Olfactory white matter
lot               180                            lateral olfactory tract
cc-ec-cing-dwm     67  corpus callosum and associated subcortical whi...
ac               1002                                Anterior commissure
aca                36                 anterior commissure, anterior limb
acp                37                anterior commissure, posterior limb
aci                73              anterior commissure, intrabulbar part
hiw              1003                           Hippocampal white matter
alv                 6                          alveus of the hippocampus
vhc                38                     ventral hippocampal commissure
f                  52                                             fornix
fi                 59                         fimbria of the hippocampus
cfp              1004                              Corticofugal pathways
ic-cp-lfp-py        1              corticofugal tract and corona radiata
pyx                85                              pyramidal decussation
ml               1005                                   Medial lemniscus
ml-u               34                      medial lemniscus, unspecified
mlx                84                       medial lemniscus decussation
tht              1006                                    Thalamic tracts
eml              1051                          External medullary lamina
eml-u             249             external medullary lamina, unspecified
eml-ar            157      external medullary lamina, auditory radiation
iml               291                          internal medullary lamina
ima               290                       intramedullary thalamic area
scp-pr            270   superior cerebellar peduncle and prerubral field
ptl               239                            pretectothalamic lamina
mtg                53                            mammillotegmental tract
cst                54                       commissural stria terminalis
fr                 60                             fasciculus retroflexus
sm                 61                           stria medullaris thalami
st                 62                                   stria terminalis
hbc                80                               habenular commissure
pc                 63                               posterior commissure
7n               1007                                       Facial nerve
7n-u               35                          facial nerve, unspecified
asc7               72               ascending fibers of the facial nerve
g7                 57                           genu of the facial nerve
ofs              1008      Optic fiber system and supraoptic decussation
2n                 41                                        optic nerve
opt-och            42                       optic tract and optic chiasm
sox                83                             supraoptic decussation
tew              1009                         White matter of the tectum
csc                46              commissure of the superior colliculus
bsc                68                brachium of the superior colliculus
cic                69                    inferior colliculus, commissure
bic               146                      inferior colliculus, brachium
cbt              1010          Cerebellar and precerebellar white matter
icp                 7                       inferior cerebellar peduncle
mcp                78                         middle cerebellar peduncle
tfp                79                      transverse fibers of the pons
bsw 

In [34]:
from pandas.testing import assert_frame_equal

SINGLE_CHANNEL_GAP = 20 # When histo contains only "span", we need to add this between structures to match the channel based def

# def get_sglx_file_counterparts(
#     project: SGLXProject,
#     subject: str,
#     paths: list[pathlib.Path],
#     extension: str,
#     remove_probe: bool = False,
#     remove_stream: bool = False,
# ) -> list[pathlib.Path]:
def save_structure_files(dat, save=False, overwrite=False):
    
    subjectName = dat["subjectName"]
    probe = dat["probe"]
    histo = dat["histo"]
    # hippo = dat.get("hippo", None)
    
    sglxSubject = wet.get_sglx_subject(subjectName)
    sglxProject = wet.get_wne_project(lfpProjectName)
    
    print(histo)

    if "loChIx" in histo:

        # ap_table = sglxSubject.get_ap_bin_table(experiment, "full", probe=probe)
        # ap_file = ap_table.iloc[0].path
        # print(ap_file)
        # im = sglxr.ImecMap.from_bin(ap_file)
        lfp_table = sglxSubject.get_lfp_bin_table(experiment, "full", probe=probe)
        lfp_file = lfp_table.iloc[0].path
        # [nc_file] = sglxProject.get_sglx_counterparts(sglxSubject.name, [lfp_file], wne.constants.NETCDF_EXT)
        [nc_file] = get_sglx_file_counterparts(sglxProject, sglxSubject.name, [lfp_file], wne.constants.NETCDF_EXT)
        if nc_file.is_file():
            lf = xr.open_dataarray(nc_file)
            y = lf.y.values
        elif lfp_file.is_file():
            im = sglxr.ImecMap.from_bin(lfp_file)
            y = im.y
        else:
            raise FileNotFoundError

        histo['lo'] = y[histo['loChIx']]
        histo['hi'] = y[histo['hiChIx']]
        histo['span'] = histo['hi'] - histo['lo']
        histo = histo[['structure', 'acronym', 'lo', 'hi', 'span']]

    elif "span" in histo and not "lo" in histo:
        
        raise ValueError("Don't use span because errors accumulate... use loChIx/HiChIx")
        
        # span = np.array(histo["span"])
        # lo = np.cumsum(np.insert(span[::-1], 0, 0)[:-1])[::-1] # Cumsum in reverse order, starting from 0
        # print(np.arange(0, SINGLE_CHANNEL_GAP * len(lo) + 1, SINGLE_CHANNEL_GAP))
        # lo = lo + np.arange(0, SINGLE_CHANNEL_GAP * len(lo), SINGLE_CHANNEL_GAP)[::-1] # Add 1-channel gap between successive regions
        # print(np.arange(0, SINGLE_CHANNEL_GAP * len(lo) + 1, SINGLE_CHANNEL_GAP))
        # print(lo)
        # hi = lo + span
        # histo["lo"] = lo
        # histo["hi"] = hi
    
    assert set(histo.columns.values) == {"structure", "acronym", "lo", "hi", "span"}
    assert np.all((histo.hi - histo.lo) == histo.span)

    f = wneAnatomyProject.get_experiment_subject_file(experiment, sglxSubject.name, f"{probe}.structures.htsv")
    
    print("\n", histo, "\n")    
    
    print(f)
    print("file exists: ", f.exists(), "\n\n")
    

    get_matching_structures_from_atlas(
        histo.structure, histo.acronym
    )
    
    # if True:
    if save:
        if f.exists():
            if not overwrite:
                previous = utils.read_htsv(f)
                assert_frame_equal(histo, previous)
                print("file equal: True")
        print("saving")
        utils.write_htsv(histo, f)
        
def get_matching_structures_from_atlas(structures, acronyms, atlas_name="whs_sd_rat_39um"):
    from bg_atlasapi.bg_atlas import BrainGlobeAtlas
    from thefuzz import process
    from thefuzz import fuzz
    atlas = BrainGlobeAtlas(atlas_name, brainglobe_dir="/Volumes/npx_nfs/shared_s3/.brainglobe")

    pd.set_option('display.max_rows', None)
    atlas_df = atlas.lookup_df
    
    to_match = [', '.join(i) for i in zip(structures, acronyms)]
    choices = [', '.join(i) for i in zip(atlas_df["name"], atlas_df["acronym"])]
    for i, acronym in enumerate(acronyms):
        if not acronym in atlas_df.acronym.values:
            print("ACRONYM DOESNT EXIST IN ATLAS:")
            print(structures[i], acronym)
            print("some options: ", process.extract(to_match[i], choices, limit=15, scorer=fuzz.partial_token_sort_ratio))
            print('\n')
    
def load_sorting(dat):
    subjectName = dat["subjectName"]
    probe = dat["probe"]
    histo = dat["histo"]
    # hippo = dat.get("hippo", None)
    
    sglxSubject = wet.get_sglx_subject(subjectName)
    
    # Plot cluster distribution
    from ecephys.wne.sglx.utils import load_singleprobe_sorting
    
    sorting = load_singleprobe_sorting(
        wet.get_sglx_project("shared_sortings"),
        sglxSubject,
        experiment,
        alias,
        probe,
        wneAnatomyProject = wet.get_wne_project("shared_s3"),
        allow_no_sync_file=True,            
    ).refine_clusters(
        {"quality": {"good", "mua"}},
        include_nans=True,
    )
    return sorting


def plot_cluster_distribution(dat):
        
    sorting = load_sorting(dat)

    import altair as alt
    c = alt.Chart(sorting.properties).mark_bar().encode(
        x=alt.X("depth", bin=alt.Bin(step=20)),
        y="count()",
        color="acronym",
    )
    
    structs = sorting.si_obj.get_annotation("structure_table")
    c = c + alt.Chart(structs).mark_rule().encode(
        x = "lo"
    ) + alt.Chart(structs).mark_rule().encode(
        x = "hi"
    )
    return c.properties(
        width=2000,
        height=500,
    ).configure_legend( titleFontSize=22, labelFontSize=20 )

Doppio frontal:
- 53 channels outside of the brain
- M2 (Wax and Pax): 2000 um; channels 232 to 331
- Prelimbic(Wax) or A32D and V (Pax): channels 107 to 230
- Medial orbital cortex (MO: Pax Wax): 62 to 105
- Olfactory area or Basal Forebrain (Wax) or Dorsa tenia tecta (Pax: DTT): 1400 um; channels 1 to 60 

In [74]:
dat = {
    "subjectName": "CNPIX4-Doppio",
    "probe": "imec1",
    "histo": pd.DataFrame(
        {
            "structure": [
#                 "Out of brain",
                "Secondary motor area",
                "Prelimbic area / A32D + A32V",
                "Medial orbital area",
                "Olfactory area / Basal forebrain / Dorsia tenia tecta",  # TODO
            ],
#             "acronym": ["M2", "PrL", "MO", "OA/BF/DTT"],
              "acronym": ["M2", "PrL", "MO", "BRF"],

#             "loChIx": [231, 106, 61, 0],
            "loChIx": [231, 106, 60, 0],
            "hiChIx": [330, 229, 104, 59],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=False)

                                           structure acronym  loChIx  hiChIx
0                               Secondary motor area      M2     231     330
1                       Prelimbic area / A32D + A32V     PrL     106     229
2                                Medial orbital area      MO      60     104
3  Olfactory area / Basal forebrain / Dorsia teni...     BRF       0      59

                                            structure acronym      lo      hi  \
0                               Secondary motor area      M2  4620.0  6600.0   
1                       Prelimbic area / A32D + A32V     PrL  2120.0  4580.0   
2                                Medial orbital area      MO  1200.0  2080.0   
3  Olfactory area / Basal forebrain / Dorsia teni...     BRF     0.0  1180.0   

     span  
0  1980.0  
1  2460.0  
2   880.0  
3  1180.0   

/Volumes/npx_nfs/shared_s3/novel_objects_deprivation/CNPIX4-Doppio/imec1.structures.htsv
file exists:  True 


file equal: True
saving


In [39]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:106: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 224 clusters.
224/855 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Doppio parietal

- PtA: 1440 um; channels 300 to 374
- WM: 220 um; channels 288 to 298
- Hipp: 1880 um; channels 192 to 286 (channel 278 = CA1)
- Thalamus (LPMR): 900 um ; channels 144 to 190
- Thalamus (Po): 1420 um; channels 71 to 142
- Thalamus (VPM): 1000 um; channels 19 to 69
- Hipo (ZI + Lem): 360 um; channels 1 to 18
- Tip: 180 um.

In [75]:
dat = {
    "subjectName": "CNPIX4-Doppio",
    "probe": "imec0",
    "histo": pd.DataFrame({
            "structure": [
                "Medial parietal association cortex",
                "White matter",
                "Hippocampus",
#                 "Mediorostral lateroposterior thalamic nucleus",
                "Lateral posterior thalamic nucleus",
                "Posterior thalamic nucleus",
                "Ventral posteromedial nucleus",
                "Zona incerta",
            ],
#             "acronym": ["MPtA", "WM", "HC", "LPMR", "Po", "VPM", "ZI"],
            "acronym": ["mPPC", "wmt", "HR", "LP-mr", "Po", "VPM", "ZI"],

            # "span": [1440, 220, 1880, 900, 1420, 1000, 360],
            "loChIx": [299, 287, 191, 143, 70, 18, 0],
            "hiChIx": [373, 297, 285, 189, 141, 68, 17],
    }),
    "hippo": pd.DataFrame({
            "structure": [
                "CA1 stratum pyramidale and stratum oriens",
                "CA1 stratum radiatum",
                "CA1 stratum lacunosum moleculare",
                "Dorsal dentate gyrus",
                "CA3",
                "Ventral dentate gyrus",
            ],
            'acronym': ['poCA1', 'srCA1', 'slmCA1', 'dDG', 'CA3', 'vDG'],
            'hi': [5760, 5500, 5220, 4940, 4660, 4340],
            'lo': [5500, 5220, 4940, 4660, 4340, 3900],
    }),
}

save_structure_files(dat, save=False)

                            structure acronym  loChIx  hiChIx
0  Medial parietal association cortex    mPPC     299     373
1                        White matter     wmt     287     297
2                         Hippocampus      HR     191     285
3  Lateral posterior thalamic nucleus   LP-mr     143     189
4          Posterior thalamic nucleus      Po      70     141
5       Ventral posteromedial nucleus     VPM      18      68
6                        Zona incerta      ZI       0      17

                             structure acronym      lo      hi    span
0  Medial parietal association cortex    mPPC  5980.0  7460.0  1480.0
1                        White matter     wmt  5740.0  5940.0   200.0
2                         Hippocampus      HR  3820.0  5700.0  1880.0
3  Lateral posterior thalamic nucleus   LP-mr  2860.0  3780.0   920.0
4          Posterior thalamic nucleus      Po  1400.0  2820.0  1420.0
5       Ventral posteromedial nucleus     VPM   360.0  1360.0  1000.0
6           

In [41]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:106: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 47 clusters.
47/326 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Luigi parietal
- 29 channels outside the brain
- PtA: 1540 um; channels 287 to 355
- WM: 290 um; channels  to 274: 285
- Hipp: 1840 um; channels 180 to 272  (channel 262  = CA1) 
- Thalamus dorsal lateral geniculate nucleus:  960 um ; channels  129 to 177
- Thalamus medial geniculate body: 1230 um ; channels  65 to 127
- Thalamus posterior intralaminar nucleus: 193 um; channels 54 to 63 
- Corticofugal tract and corona radiata:  810 um; channels 12 to 53
- Cornu ammonis: 210 um; channels 1 to 10
- + Tip: 180 um. Cornu ammonis


In [76]:
dat = {
    "subjectName": "CNPIX9-Luigi",
    "probe": "imec0",
    "histo": pd.DataFrame({
            "structure": [
                "Parietal association cortex", # TODO
                "White matter",
                "Hippocampus",
                "Thalamus dorsal lateral geniculate nucleus",
                "Thalamus medial geniculate body",
                "Thalamus posterior intralaminar nucleus",
                "Corticofugal tract and corona radiata",
                "Cornu ammonis",
            ],
            "acronym": [
                "mPPC",
                "wmt",
                "HR",
                "DLG",
                "MG",
                "PIL",
                "ic-cp-lfp-py",
                "CA",
            ], # TODO
            "loChIx": [286, 273, 179, 128, 64, 53, 11,  0],
            "hiChIx": [354, 284, 271, 176, 126, 62, 52, 9],
    }),
    "hippo": None,
}

save_structure_files(dat, save=False)

                                    structure       acronym  loChIx  hiChIx
0                 Parietal association cortex          mPPC     286     354
1                                White matter           wmt     273     284
2                                 Hippocampus            HR     179     271
3  Thalamus dorsal lateral geniculate nucleus           DLG     128     176
4             Thalamus medial geniculate body            MG      64     126
5     Thalamus posterior intralaminar nucleus           PIL      53      62
6       Corticofugal tract and corona radiata  ic-cp-lfp-py      11      52
7                               Cornu ammonis            CA       0       9

                                     structure       acronym      lo      hi  \
0                 Parietal association cortex          mPPC  5720.0  7080.0   
1                                White matter           wmt  5460.0  5680.0   
2                                 Hippocampus            HR  3580.0  5420.0  

In [12]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/utils.py:150: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 72 clusters.
72/146 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Charles imec0

- 29 channels outside of the brain
- M2 (Pax and Wax): 254-355
- Cingulate area 1 (Wax) or A32D (Pax: cingulate cortex area 32): 460 um; channels 227 to 250;
- Prelimbic (Wax) or A32D and A32V (Pax: cingulate cortex):960 um; channels 175 to 223
- White matter (Pax and Wax) : 200 um; channels 170 to 180 I find it difficult to estimate the corpus callosum.
- Claustrum (Pax and Wax):  1240 um; channels 100 to 168
- Ventral orbital area: 460 um; channels 72 to 110
- Ventricular system: 160um; channels 62 to 70
- Nucleus Acumbens: 1150 um, channels1 to 60
-180 um tip


In [80]:
dat = {
    "subjectName": "CNPIX10-Charles",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
#                 "Out of brain",
                "Secondary motor cortex",
                "Cingulate area 1 (Wax) or A32D (Pax: cingulate cortex area 32)",
                "Prelimbic (Wax) or A32D and A32V (Pax: cingulate cortex)",
                "White matter",
                "Claustrum",
                "Ventral orbital area",
                "Ventricular system",
                "Nucleus Acumbens",
            ],
            "acronym": ["M2", "Cg1", "PrL", "wmt", "CLA", "VO", "V", "NAc"],
#             "loChIx": [253, 226, 174, 169, 99, 71, 61, 0],
#             "hiChIx": [354, 249, 222, 179, 167, 109, 69, 59],
            "loChIx": [253, 226, 174, 169, 99, 71, 61, 0],
            "hiChIx": [354, 249, 222, 179, 167, 98, 69, 59],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=False)

                                           structure acronym  loChIx  hiChIx
0                             Secondary motor cortex      M2     253     354
1  Cingulate area 1 (Wax) or A32D (Pax: cingulate...     Cg1     226     249
2  Prelimbic (Wax) or A32D and A32V (Pax: cingula...     PrL     174     222
3                                       White matter     wmt     169     179
4                                          Claustrum     CLA      99     167
5                               Ventral orbital area      VO      71      98
6                                 Ventricular system       V      61      69
7                                   Nucleus Acumbens     NAc       0      59

                                            structure acronym      lo      hi  \
0                             Secondary motor cortex      M2  5060.0  7080.0   
1  Cingulate area 1 (Wax) or A32D (Pax: cingulate...     Cg1  4520.0  4980.0   
2  Prelimbic (Wax) or A32D and A32V (Pax: cingula...     PrL  348

In [29]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/utils.py:150: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 98 clusters.
98/553 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Charles imec1

- 10 channels outside the brain
- PtA: 1580 um; channels 295 to 374
- WM: 277 um; channels  to 284: 293
- Hipp: 1670 um; channels 198 to 282  (channel 272  = CA1)
- Thalamus (LPLR):  1045um ; channels  143 to 196
- Thalamus (Po): 815 um; channels 100 to 141 
- Thalamus (VPM):  1050 um; channels 52 to 98
- Thalamus (VPL):  530 um; channels 24 to 50
- Hipo (ZI + Lem):  375 um; channels 5 to 22
- Corticofugal tract corona radiata: 80um;  1:4
- Tip: 180 um.


In [81]:
dat = {
    "subjectName": "CNPIX10-Charles",
    "probe": "imec1",
    "histo": pd.DataFrame({
            "structure": [
                "Parietal association cortex",
                "White matter",
                "Hippocampus",
                "Thalamus (LPLR)",
                "Thalamus (Po)",
                "Thalamus (VPM)",
                "Thalamus (VPL)",
                "Hypo (ZI + Lem)",
                "Corticofugal tract corona radiata",
            ],
            "acronym": [
                "mPPC",
                "wmt",
                "HR",
                "LP-l",
                "Po",
                "VPM",
                "VPL",
                "HY",
                "ic-cp-lfp-py",
            ],
#             "loChIx": [294, 283, 197, 142, 99, 51, 23, 4, 0],
            "loChIx": [294, 283, 197, 142, 98, 51, 23, 4, 0],
            "hiChIx": [375, 292, 281, 195, 140, 97, 49, 21, 3],
    }),
    "hippo": None,
}

save_structure_files(dat, save=False)

                           structure       acronym  loChIx  hiChIx
0        Parietal association cortex          mPPC     294     375
1                       White matter           wmt     283     292
2                        Hippocampus            HR     197     281
3                    Thalamus (LPLR)          LP-l     142     195
4                      Thalamus (Po)            Po      98     140
5                     Thalamus (VPM)           VPM      51      97
6                     Thalamus (VPL)           VPL      23      49
7                    Hypo (ZI + Lem)            HY       4      21
8  Corticofugal tract corona radiata  ic-cp-lfp-py       0       3

                            structure       acronym      lo      hi    span
0        Parietal association cortex          mPPC  5880.0  7500.0  1620.0
1                       White matter           wmt  5660.0  5840.0   180.0
2                        Hippocampus            HR  3940.0  5620.0  1680.0
3                    Thalamu

In [17]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/utils.py:150: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 138 clusters.
138/291 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Adrian imec0

- 33 channels outside of the brain
- M2 (Pax and Wax): 1300um ; channels 300 to 351
- A24b (Pax) or Cingulate area 1 (Wax): 1080um ; channels 244 to 298
- A24a and A32V (Pax) Prelimbic (Wax): 1780um; channels 155 to 243
- A32V and A25 (Pax) Infralimbic(Wax): 1060um; channels 100 to 153
- Corpus callosum: 400um; channels 78 to 98
- Nucleus acumbens, shell (Pax and Wax):  1520um; channels 1 to 76
- 180um tip


In [82]:
dat = {
    "subjectName": "CNPIX11-Adrian",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
#                 "Out of brain",
                "Secondary motor cortex",
                "A24b (Pax) or Cingulate area 1 (Wax)",
                "A24a and A32V (Pax) Prelimbic (Wax)",
                "A32V and A25 (Pax) Infralimbic(Wax)",
                "Corpus callosum",
                "Nucleus acumbens, shell",
            ],
            "acronym": ["M2", "Cg1", "PrL", "IL", "cc-ec-cing-dwm", "NAc-sh"],
            "loChIx": [299, 243, 154, 99, 77, 0],
            "hiChIx": [350, 297, 242, 152, 97, 75],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=True)

                              structure         acronym  loChIx  hiChIx
0                Secondary motor cortex              M2     299     350
1  A24b (Pax) or Cingulate area 1 (Wax)             Cg1     243     297
2   A24a and A32V (Pax) Prelimbic (Wax)             PrL     154     242
3   A32V and A25 (Pax) Infralimbic(Wax)              IL      99     152
4                       Corpus callosum  cc-ec-cing-dwm      77      97
5               Nucleus acumbens, shell          NAc-sh       0      75

                               structure         acronym      lo      hi  \
0                Secondary motor cortex              M2  5980.0  7000.0   
1  A24b (Pax) or Cingulate area 1 (Wax)             Cg1  4860.0  5940.0   
2   A24a and A32V (Pax) Prelimbic (Wax)             PrL  3080.0  4840.0   
3   A32V and A25 (Pax) Infralimbic(Wax)              IL  1980.0  3040.0   
4                       Corpus callosum  cc-ec-cing-dwm  1540.0  1940.0   
5               Nucleus acumbens, shell     

In [53]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:106: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 165 clusters.
165/360 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Adrian imec1:

- Channels 354 to 384 are bad channels
- PtA-V2: 1580 um; channels 320 to 353
- WM: 185 um; channels  311 to 319: 
- Hipp: 1960 um; channels 212 to 310  (channel 300  = CA1)
- Thalamus (LPLR):  1115 um ; channels  154 to 210
- External medullary lamina: 160um; channels 144 to 152
- Posteriror thalamic nucleus (Po): 1115 um; channels 86 to 142 
- Medial lemniscus: 246um; channels 72 to 84
- Zona Incerta caudal part: 1082 um; channels 16 to 70
- Sustancia Negra:  245um; channels 4 to 15
- Corticofugal tract corona radiata: 80um;  1:3
- Tip: 180 um. Corticofugal tract


In [107]:
dat = {
    "subjectName": "CNPIX11-Adrian",
    "probe": "imec1",
    "histo": pd.DataFrame({
            "structure": [
                "Parietal association cortex - V2",
                "White matter",
                "Hippocampus",
                "Thalamus (LPLR)",  # TODO
                "External medullary lamina",
                "Posteroior thalamic nucleus",
                "Medial lemniscus",
                "Zona Incerta (caudal part)",
                "Substancia negra",
                "Corticofugal tract corona radiata",
            ],
            "acronym": [
                "mPPC",
                "wmt",
                "HR",
                "LP-l",
                "eml",
                "Po",
                "ml",
                "ZI-c",
                "SN",
                "ic-cp-lfp-py"
            ], # TODO
            "loChIx": [319, 310, 211, 153, 143, 85, 71, 15, 3, 0],
            "hiChIx": [352, 318, 309, 209, 151, 141, 83, 69, 14, 2],
    }),
    "hippo": None,
}

save_structure_files(dat, save=True, overwrite=True)

                           structure       acronym  loChIx  hiChIx
0   Parietal association cortex - V2          mPPC     319     352
1                       White matter           wmt     310     318
2                        Hippocampus            HR     211     309
3                    Thalamus (LPLR)          LP-l     153     209
4          External medullary lamina           eml     143     151
5        Posteroior thalamic nucleus            Po      85     141
6                   Medial lemniscus            ml      71      83
7         Zona Incerta (caudal part)          ZI-c      15      69
8                   Substancia negra            SN       3      14
9  Corticofugal tract corona radiata  ic-cp-lfp-py       0       2

                            structure       acronym      lo      hi    span
0   Parietal association cortex - V2          mPPC  6380.0  7040.0   660.0
1                       White matter           wmt  6200.0  6360.0   160.0
2                        Hippocampus

In [106]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:106: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 52 clusters.
52/186 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Santiago frontal

- 26 channels outside de brain,
- M2 (Pax and Wax): 2300um; channels 246 to 359.,
- Ventral Orbital area (Wax) or Ventral orbital cortex (Pax: Vo): 1740um channels 157 to 244.,
- Olfactory area (Wax) or Pir or anterior olfactory area (Pax) dorsal part: channels 105 to 154,
- Anterior commissure (Pax and Wax): 420um ; channels 82 to 103,
- Olfactory area (Wax) or Pir or anterior olfactory area (Pax) ventral part: 1540 um; channels 3 to 80,


In [38]:
dat = {
    "subjectName": "CNPIX12-Santiago",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
                "M2 (Pax and Wax)",
                "Ventral Orbital area (Wax) or Ventral orbital cortex (Pax: Vo)",
                "Olfactory area (Wax) or Pir or anterior olfactory area (Pax) dorsal part",
                "Anterior commissure (Pax and Wax)",
                "Olfactory area (Wax) or Pir or anterior olfactory area (Pax) ventral part",
            ],
            "acronym": ["M2", "VO", "OB", "ac", "OB"],
            "loChIx": [245, 156, 104, 81, 2],
            "hiChIx": [358, 243, 153, 102, 79],
        }
    ),
}

save_structure_files(dat, save=False)

                                           structure acronym  loChIx  hiChIx
0                                   M2 (Pax and Wax)      M2     245     358
1  Ventral Orbital area (Wax) or Ventral orbital ...      VO     156     243
2  Olfactory area (Wax) or Pir or anterior olfact...      OB     104     153
3                  Anterior commissure (Pax and Wax)      ac      81     102
4  Olfactory area (Wax) or Pir or anterior olfact...      OB       2      79

                                            structure acronym      lo      hi  \
0                                   M2 (Pax and Wax)      M2  4900.0  7160.0   
1  Ventral Orbital area (Wax) or Ventral orbital ...      VO  3120.0  4860.0   
2  Olfactory area (Wax) or Pir or anterior olfact...      OB  2080.0  3060.0   
3                  Anterior commissure (Pax and Wax)      ac  1620.0  2040.0   
4  Olfactory area (Wax) or Pir or anterior olfact...      OB    40.0  1580.0   

     span  
0  2260.0  
1  1740.0  
2   980.0  
3   420

In [39]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:105: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 67 clusters.
67/484 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Santiago parietal


- 26 channels outside de brain
- PtA (Pax and Wax): 1520um; channels 292 to 367.
- With Matter: 250um; channels 278 to 290
- Hippocampus: 1840um; channels 186 to 276
- Laterodorsal thalamic nucleus (Wax) or LPMR-VL (Pax): 1060 um; channels 132 to 184 
- Posterior thalamic nucleus (Wax) or Po (Pax): 1360um; channels 62 to 130
- Ventrolateral thalamic nucleus (Wax) or VL (Pax): 320 um; channels 44 to 60
- Ventromedial thalamic nucleus (Wax) or VM (Pax): 506um; channels 14 to 42.
- Zona Incerta (Pax and Wax): 250um; channels 1 to 12.
Tip 180um



In [84]:
dat = {
    "subjectName": "CNPIX12-Santiago",
    "probe": "imec1",
    "histo": pd.DataFrame(
        {
            "structure": [
#                 "Out of brain",
                "Medial parietal association cortex",
                "White matter",
                "Hippocampus",
                "Laterodorsal thalamic nucelus / Mediorostral lateroposterior thalamic nucleus",
                "Posterior thalamic nucleus",
                "Ventrolateral thalamic nucleus",
                "Ventromedial thalamic nucleus",
                "Zona incerta",
            ],
#             "acronym": ["OOB", "MPtA", "WM", "HC", "LD/LPMR", "Po", "VL", "VM", "ZI"],
#             "loChIx": [368, 291, 277, 185, 131, 61, 43, 13, 0],
#             "hiChIx": [383, 367, 290, 276, 184, 130, 60, 42, 12],
            "acronym": ["mPPC", "wmt", "HR", "LD", "Po", "VL", "VM", "ZI"],
            "loChIx": [291, 277, 185, 131, 61, 43, 13, 0],
            "hiChIx": [366, 289, 275, 183, 129, 59, 41, 12],
        }
    ),
    "hippo": pd.DataFrame(
        {
            "structure": [
                "ca1 stratum pyramidale and stratum oriens",
                "ca1 stratum radiatum",
                "ca1 stratum lacunosum moleculare",
                "dorsal dentate gyrus",
                "ca3",
                "ventral dentate gyrus",
            ],
            'acronym': ['poca1', 'srca1', 'slmca1', 'spdg', 'ca3', 'ipdg'],
            'hi': [5540, 5240, 4940, 4680, 4320, 4000],
            'lo': [5240, 4940, 4700, 4500, 4180, 3540],
        }
    )
}

save_structure_files(dat)

                                           structure acronym  loChIx  hiChIx
0                 Medial parietal association cortex    mPPC     291     366
1                                       White matter     wmt     277     289
2                                        Hippocampus      HR     185     275
3  Laterodorsal thalamic nucelus / Mediorostral l...      LD     131     183
4                         Posterior thalamic nucleus      Po      61     129
5                     Ventrolateral thalamic nucleus      VL      43      59
6                      Ventromedial thalamic nucleus      VM      13      41
7                                       Zona incerta      ZI       0      12

                                            structure acronym      lo      hi  \
0                 Medial parietal association cortex    mPPC  5820.0  7320.0   
1                                       White matter     wmt  5540.0  5780.0   
2                                        Hippocampus      HR  370

In [23]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/utils.py:150: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 84 clusters.
84/342 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Al frontal

- 4 channels outside of the brain
- M2 (Pax and Wax): 1300um ; channels 291 to 380
- Ventral orbital area (Pax and Wax): 1300um ; channels 181 to 289
-  Pir or AON (Pax) Olfactory area(Wax): 3550um ; channels 24 to 179
- Channels 1to 25 probably outside of the brain (EMG during Wake)
- Tip 180 um


In [85]:
dat = {
    "subjectName": "CNPIX13-Al",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Secondary motor cortex (Pax and Wax)",
                "Ventral orbital area (Pax and Wax)",
                "Pir or AON (Pax) Olfactory area (Wax)",
            ],
            "acronym": ["M2", "VO", "OB"],
            "loChIx": [290, 180, 23],
            "hiChIx": [379, 288, 178],
        }
    ),
}

save_structure_files(dat)

                               structure acronym  loChIx  hiChIx
0   Secondary motor cortex (Pax and Wax)      M2     290     379
1     Ventral orbital area (Pax and Wax)      VO     180     288
2  Pir or AON (Pax) Olfactory area (Wax)      OB      23     178

                                structure acronym      lo      hi    span
0   Secondary motor cortex (Pax and Wax)      M2  5800.0  7580.0  1780.0
1     Ventral orbital area (Pax and Wax)      VO  3600.0  5760.0  2160.0
2  Pir or AON (Pax) Olfactory area (Wax)      OB   460.0  3560.0  3100.0 

/Volumes/npx_nfs/shared_s3/novel_objects_deprivation/CNPIX13-Al/imec0.structures.htsv
file exists:  False 


saving


In [62]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:106: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


FileNotFoundError: Segment table not found at /Volumes/npx_nfs/shared_sortings/novel_objects_deprivation/full/CNPIX13-Al/sorting.imec0/segments.htsv.

Francis parietal:
- Secondary visual cortex (Pax and Wax): 1400um; channels 311 to 384
- WM (Pax and Wax): 155um, channels 305 to 310
- CA1 (pax and Wax): 720um; channels 274 to 304
- Dentate Gyrus (Pax and Wax): 1180um; channels 213 to 272
- Lateral posterior thalamic nucleus (Pax and Wax): 982um; channels 170 to 211
- Posterior thalamic nucleus (Pax and Wax): 1500um; channels 93 to 168
- Medial lemniscus (Pax and Wax): 240 um; channels 80 to 91
- Zona Incerta (Pax and Wax): 900um; channels 35 to 78
- Substantia nigra (Pax and Wax): 140um; channels 27 to 33
- Corticofugal tract (Wax) or cerebral peduncle (Pax): 500um; channels 1 to 25

In [87]:
dat = {
    "subjectName": "CNPIX14-Francis",
    "probe": "imec1",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Secondary visual cortex",
                "White matter",
                "CA1",
                "Dentate gyrus",
                "Lateral posterior thalamic nucleus",
                "Posterior thalamic nucleus",
                "Medial lemniscus",
                "Zona incerta",
                "Substantia nigra",
                "Corticofugal tract",
            ],
            "acronym": ["V2", "wmt", "CA1", "DG", "LP", "Po", "ml", "ZI", "SN", "cfp"],
            # "span": [1400, 155, 720, 1180, 982, 1500, 240, 900, 140, 500],
            "loChIx": [310, 304, 273, 212, 169, 92, 79, 34, 26, 0],
            "hiChIx": [383, 309, 303, 271, 210, 167, 90, 77, 32, 24],
        }
    ),
    "hippo": pd.DataFrame(
        {
            "structure": [
                "CA1 stratum pyramidale and stratum oriens",
                "CA1 stratum radiatum",
                "CA1 stratum lacunosum moleculare",
                "Dorsal dentate gyrus",
                "CA3/DG",
                "Ventral dentate gyrus",
            ],
            'acronym': ['poCA1', 'srCA1', 'slmCA1', 'dDG', 'CA3-DG', 'vDG'],
            'hi': [6040, 5760, 5500, 5220, 4940, 4700],
            'lo': [5760, 5500, 5220, 4940, 4700, 4140],
        }
    ),
}

save_structure_files(dat, save=False, overwrite=False)

                            structure acronym  loChIx  hiChIx
0             Secondary visual cortex      V2     310     383
1                        White matter     wmt     304     309
2                                 CA1     CA1     273     303
3                       Dentate gyrus      DG     212     271
4  Lateral posterior thalamic nucleus      LP     169     210
5          Posterior thalamic nucleus      Po      92     167
6                    Medial lemniscus      ml      79      90
7                        Zona incerta      ZI      34      77
8                    Substantia nigra      SN      26      32
9                  Corticofugal tract     cfp       0      24

                             structure acronym      lo      hi    span
0             Secondary visual cortex      V2  6200.0  7660.0  1460.0
1                        White matter     wmt  6080.0  6180.0   100.0
2                                 CA1     CA1  5460.0  6060.0   600.0
3                       Dentate gyru

In [25]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/utils.py:150: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 25 clusters.
25/414 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Claude frontal

- Cx: Wax and Pax M2, 2150, 106, 276:382,
- White matter , 610, 30, 245:275,  <= Manually edited hiChIx to catch 4 more M2 units
- Caudate Putamen, 3600, 180, 64:244,
- Nucleus Accumbens Core, 750, 37, 26:63,
- Nucleus Accumbens Shell or Ventral Striatal Region, 500, 25, 0:25,



In [24]:
dat = {
    "subjectName": "CNPIX15-Claude",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Cx: Wax and Pax M2",
                "White matter",
                "Caudate Putamen",
                "Nucleus Accumbens Core",
                "Nucleus Accumbens Shell or Ventral striatal region",
            ],
            "acronym": ["M2", "wmt", "CPu", "NAc-c", "Str"],
            "loChIx": [267, 245, 64, 26, 0],
            "hiChIx": [382, 266, 244, 63, 25],
            # "loChIx": [276, 245, 64, 26, 0],
            # "hiChIx": [382, 275, 244, 63, 25],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=False)

                                           structure acronym  loChIx  hiChIx
0                                 Cx: Wax and Pax M2      M2     267     382
1                                       White matter     wmt     245     266
2                                    Caudate Putamen     CPu      64     244
3                             Nucleus Accumbens Core   NAc-c      26      63
4  Nucleus Accumbens Shell or Ventral striatal re...     Str       0      25

                                            structure acronym      lo      hi  \
0                                 Cx: Wax and Pax M2      M2  5340.0  7640.0   
1                                       White matter     wmt  4900.0  5320.0   
2                                    Caudate Putamen     CPu  1280.0  4880.0   
3                             Nucleus Accumbens Core   NAc-c   520.0  1260.0   
4  Nucleus Accumbens Shell or Ventral striatal re...     Str     0.0   500.0   

     span  
0  2300.0  
1   420.0  
2  3600.0  
3   740

In [22]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:105: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 108 clusters.
108/356 clusters excluded by jointly applying filters.


alt.LayerChart(...)

In [17]:
sub.properties.depth

0    5360.0
1    5460.0
2    5380.0
3    5340.0
Name: depth, dtype: float64

Claude parietal
- Cx: Wax and Pax V1, 1434,  306:377
- White matter , 207, 295:305,
- Hipp: Wax and Pax CA1, 698, 260:294,
- Hipp: Wax and Pax DG-CA3 , 1301, 194:259,
- Thalamus: Pax and Wax Dorsal lateral Geniculate Nucleus (DLG), 868, 149:193,
- Thalamus: Pax and Wax Medial Geniculate Nucleus or Body (MGN), 1283, 84:148,
- Wax Suprageniculate Nuc or Zona Incerta caudal; Pax  Zona Incerta caudal or peri peduncular nucleus, 490, 59:83,
- Wax Corticofugal tract and/or Substantia Nigra lateral; Pax cerebral Peduncle and/or Substantia Nigra lateral, 679, 24:58,
- Hipp: CA3 Cornu Ammonis, 430, 1:23,
- Tip, 170, 0,


In [16]:
dat = {
    "subjectName": "CNPIX15-Claude",
    "probe": "imec1",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Cx: Wax and Pax V1",
                "White matter",
                "Hipp: Wax and Pax CA1",
                "Hipp: Wax and Pax DG-CA3", # -> Hippocampal formation
                "Thalamus: Pax and Wax Dorsal lateral Geniculate Nucleus (DLG)",
                "Thalamus: Pax and Wax Medial Geniculate Nucleus or Body (MGN)",
                "Wax Suprageniculate Nuc or Zona Incerta caudal; Pax  Zona Incerta caudal or peri peduncular nucleus",  # TODO
                "Wax Corticofugal tract and/or Substantia Nigra lateral; Pax cerebral Peduncle and/or Substantia Nigra lateral",
                "Hipp: CA3 Cornu Ammonis",
            ],
            "acronym": ["V1", "wmt", "CA1", "HF", "DLG", "MG", "ZI-c", "SN", "CA3"],
            "loChIx": [305, 294, 259, 193, 148, 83, 58, 23, 0],
            "hiChIx": [376, 304, 293, 258, 192, 147, 82, 57, 22],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=True, overwrite=False)

                                           structure acronym  loChIx  hiChIx
0                                 Cx: Wax and Pax V1      V1     305     376
1                                       White matter     wmt     294     304
2                              Hipp: Wax and Pax CA1     CA1     259     293
3                           Hipp: Wax and Pax DG-CA3      HF     193     258
4  Thalamus: Pax and Wax Dorsal lateral Geniculat...     DLG     148     192
5  Thalamus: Pax and Wax Medial Geniculate Nucleu...      MG      83     147
6  Wax Suprageniculate Nuc or Zona Incerta caudal...    ZI-c      58      82
7  Wax Corticofugal tract and/or Substantia Nigra...      SN      23      57
8                            Hipp: CA3 Cornu Ammonis     CA3       0      22

                                            structure acronym      lo      hi  \
0                                 Cx: Wax and Pax V1      V1  6100.0  7520.0   
1                                       White matter     wmt  5880.0

In [17]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:105: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 62 clusters.
62/244 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Hans frontal
- Wax and Pax Primary motor cortex M1, 2507, 123, 263:385,
- Wax and Pax With Matter, 408, 20, 243:262,
- Wax and Pax Caudate Putamen, 3260, 161, 82:242,
- Wax and Pax Nuc. acumbens core, 1420, 70, 12:81,
- Wax and Pax Nuc. acumbens shell, 220, 11, 1:11,
- Tip , 170, 0, 0,


In [6]:
dat = {
    "subjectName": "CNPIX17-Hans",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Wax and Pax Primary motor cortex M1",
                "Wax and Pax White Matter",
                "Wax and Pax Caudate Putamen",
                "Wax and Pax Nuc. acumbens core",
                "Wax and Pax Nuc. acumbens shell",
            ],
            "acronym": ["M1", "wmt", "CPu", "NAc-c", "NAc-sh"],
            "loChIx": [262, 242, 81, 11, 0],
            "hiChIx": [383, 261, 241, 80, 10],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=True)

                             structure acronym  loChIx  hiChIx
0  Wax and Pax Primary motor cortex M1      M1     262     383
1             Wax and Pax White Matter     wmt     242     261
2          Wax and Pax Caudate Putamen     CPu      81     241
3       Wax and Pax Nuc. acumbens core   NAc-c      11      80
4      Wax and Pax Nuc. acumbens shell  NAc-sh       0      10

                              structure acronym      lo      hi    span
0  Wax and Pax Primary motor cortex M1      M1  5240.0  7660.0  2420.0
1             Wax and Pax White Matter     wmt  4840.0  5220.0   380.0
2          Wax and Pax Caudate Putamen     CPu  1620.0  4820.0  3200.0
3       Wax and Pax Nuc. acumbens core   NAc-c   220.0  1600.0  1380.0
4      Wax and Pax Nuc. acumbens shell  NAc-sh     0.0   200.0   200.0 

/Volumes/npx_nfs/shared_s3/novel_objects_deprivation/CNPIX17-Hans/imec0.structures.htsv
file exists:  True 




/home/tbugnon/miniconda3/envs/ecephys_dev/lib/python3.10/site-packages/thefuzz/fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


file equal: True
saving


In [15]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:105: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 69 clusters.
69/252 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Hans parietal

-  Wax and Pax secondary visual cortex V2, 1320, 64, 305:369,
- Wax and Pax white matter, 295, 14, 290:304,
- Hippocampus: Wax and Pax CA1, 859, 43, 247:289,
- Hippocampus: Wax and Pax DG, 915, 45, 202:246,
- Ventricle, 112, 6, 195:201,
- Wax and Pax brachium of the superior colliculus, 183, 9, 185:194,
- Wax and Pax Lateral Posterior thalamic nucleus , 1098, 55, 129:184,
- Wax and Pax Posterior thalamic nucleus, 1281, 64, 64:128,
- Wax and Pax medial lemniscus, 338, 17, 46:63,
- Wax and Pax Zona Incerta, 873 , 44, 1:45,
- tip, 170, 0, 0,



In [18]:
dat = {
    "subjectName": "CNPIX17-Hans",
    "probe": "imec1",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Wax and Pax secondary visual cortex V2",
                "Wax and Pax White Matter",
                "Hippocampus: Wax and Pax CA1",
                "Hippocampus: Wax and Pax DG",
                "Ventricle",
                "Wax and Pax brachium of the superior colliculus",
                "Wax and Pax Lateral Posterior thalamic nucleus",
                "Wax and Pax posterior thalamic nucleus",
                "Wax and Pax medial lemniscus",
                "Wax and Pax Zona Incerta",
            ],
            "acronym": ["V2", "wmt", "CA1", "DG", "V", "bsc", "LP", "Po", "ml", "ZI"],
            "loChIx": [304, 289, 246, 201, 194, 184, 128, 63, 45, 0],
            "hiChIx": [368, 303, 288, 245, 200, 193, 183, 127, 62, 44],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=True, overwrite=False)

                                         structure acronym  loChIx  hiChIx
0           Wax and Pax secondary visual cortex V2      V2     304     368
1                         Wax and Pax White Matter     wmt     289     303
2                     Hippocampus: Wax and Pax CA1     CA1     246     288
3                      Hippocampus: Wax and Pax DG      DG     201     245
4                                        Ventricle       V     194     200
5  Wax and Pax brachium of the superior colliculus     bsc     184     193
6   Wax and Pax Lateral Posterior thalamic nucleus      LP     128     183
7           Wax and Pax posterior thalamic nucleus      Po      63     127
8                     Wax and Pax medial lemniscus      ml      45      62
9                         Wax and Pax Zona Incerta      ZI       0      44

                                          structure acronym      lo      hi  \
0           Wax and Pax secondary visual cortex V2      V2  6080.0  7360.0   
1                

In [19]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:105: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'good', 'mua'} excludes 31 clusters.
31/154 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Pier parietal

-  Wax and Pax secondary visual cortex V2, 1500, 75, 298:374,
- Wax and Pax white matter, 440, 22, 275:297,
- Hippocampus: Wax and Pax CA1, 770, 39, 238:274,
- Hippocampus: Wax and Pax DG, 1190, 59, 178:237,
- Wax Lateral posterior thalamic nucleus, 660, 33, 144:177,
- Wax: Central lateral thalamic nucleus, 820, 41, 103:143,
- Wax: paracentral thalamic nucleus, 530, 26, 75:102,
- Wax: posterior thalamic nucleus, 450, 23, 52:74,
- Wax: ventral posterior nucleus of the thalamus, 300, 15, 37:51,
- Wax: ventromedial thalamic nucleus, 730, 36, 1:36,


In [25]:
dat = {
    "subjectName": "CNPIX18-Pier",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Wax and Pax secondary visual cortex V2",
                "Wax and Pax White Matter",
                "Hippocampus: Wax and Pax CA1",
                "Hippocampus: Wax and Pax DG",
                "Wax Lateral Posterior thalamic nucleus",
                "Wax Central lateral thalamic nucleus",
                "Wax Paracentral thalamic nucleus",
                "Wax posterior thalamic nucleus",
                "Wax ventral posterior thalamic nucleus",
                "Wax ventromedial thalamic nucleus",
            ],
            "acronym": ["V2", "wmt", "CA1", "DG", "LP", "CL", "PCN", "Po", "VPN", "VM"],
            "loChIx": [297, 274, 237, 177, 143, 102, 74, 51, 36, 0],
            "hiChIx": [373, 296, 273, 236, 176, 142, 101, 73, 50, 35],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=True)

                                structure acronym  loChIx  hiChIx
0  Wax and Pax secondary visual cortex V2      V2     297     373
1                Wax and Pax White Matter     wmt     274     296
2            Hippocampus: Wax and Pax CA1     CA1     237     273
3             Hippocampus: Wax and Pax DG      DG     177     236
4  Wax Lateral Posterior thalamic nucleus      LP     143     176
5    Wax Central lateral thalamic nucleus      CL     102     142
6        Wax Paracentral thalamic nucleus     PCN      74     101
7          Wax posterior thalamic nucleus      Po      51      73
8  Wax ventral posterior thalamic nucleus     VPN      36      50
9       Wax ventromedial thalamic nucleus      VM       0      35

                                 structure acronym      lo      hi    span
0  Wax and Pax secondary visual cortex V2      V2  5940.0  7460.0  1520.0
1                Wax and Pax White Matter     wmt  5480.0  5920.0   440.0
2            Hippocampus: Wax and Pax CA1     CA1 

In [26]:
plot_cluster_distribution(dat)

/home/tbugnon/projects/ecephys_dev/ecephys/ecephys/wne/sglx/utils.py:105: UserWarning: Maybe loading sample2time without probe-to-probe synchronization, watch out
  warnings.warn(


quality: {'mua', 'good'} excludes 137 clusters.
137/325 clusters excluded by jointly applying filters.


alt.LayerChart(...)

Otto parietal

-  Wax and Pax secondary visual cortex V2 medial, 1560, 78, 296:374,
- Wax and Pax white matter, 385, 19, 276:295,
- Hippocampus: Wax and Pax CA1, 885, 44, 231:275,
- Hippocampus: Wax and Pax DG, 1045, 53, 177:230,
- Wax Lateral posterior thalamic nucleus, 760, 38, 135:173,
- Wax: Central thalamic nucleus (lateral and paracentral), 745, 37, 97:134,
- Wax: posterior thalamic nucleus, 585, 29, 67:96,
- Wax: ventrolateral thalamic nucleus, 385, 19, 47:66,
- Wax: ventromedial thalamic nucleus, 715, 36, 10:46,
- Wax: ZI A11 dopaminergic cells, 200, 10, 0:10,


NB : Looks like this is zero-indexed so not converting from 1- to 0- index

In [95]:
dat = {
    "subjectName": "CNPIX19-Otto",
    "probe": "imec0",
    "histo": pd.DataFrame(
        {
            "structure": [
                "Wax and Pax secondary visual cortex V2 medial",
                "Wax and Pax white matter",
                "Hippocampus: Wax and Pax CA1",
                "Hippocampus: Wax and Pax DG",
                "Wax Lateral posterior thalamic nucleus",
                "Wax: Central thalamic nucleus (lateral and paracentral)",
                "Wax: posterior thalamic nucleus",
                "Wax: ventrolateral thalamic nucleus",
                "Wax: ventromedial thalamic nucleus",
                "Wax: ZI A11 dopaminergic cells",
            ],
            "acronym": ["V2", "wmt", "CA1", "DG", "LP", "ILM", "Po", "VL", "VM", "ZI-A11"],
            "loChIx": [296, 276, 231, 177, 135, 97, 67, 47, 10, 0],
            "hiChIx": [374, 295, 275, 230, 173, 134, 96, 66, 46, 10],
        }
    ),
    "hippo": None,
}

save_structure_files(dat, save=True)

                                           structure acronym  loChIx  hiChIx
0      Wax and Pax secondary visual cortex V2 medial      V2     296     374
1                           Wax and Pax white matter     wmt     276     295
2                       Hippocampus: Wax and Pax CA1     CA1     231     275
3                        Hippocampus: Wax and Pax DG      DG     177     230
4             Wax Lateral posterior thalamic nucleus      LP     135     173
5  Wax: Central thalamic nucleus (lateral and par...     ILM      97     134
6                    Wax: posterior thalamic nucleus      Po      67      96
7                Wax: ventrolateral thalamic nucleus      VL      47      66
8                 Wax: ventromedial thalamic nucleus      VM      10      46
9                     Wax: ZI A11 dopaminergic cells  ZI-A11       0      10

                                            structure acronym      lo      hi  \
0      Wax and Pax secondary visual cortex V2 medial      V2  5920.0  7

In [59]:
atlas_df

id                                               name
acronym                                                                 
root            10000                                               Root
Brain            1000                                              Brain
wmt              1001                                       White matter
olf              1050                             Olfactory white matter
lot               180                            lateral olfactory tract
cc-ec-cing-dwm     67  corpus callosum and associated subcortical whi...
ac               1002                                Anterior commissure
aca                36                 anterior commissure, anterior limb
acp                37                anterior commissure, posterior limb
aci                73              anterior commissure, intrabulbar part
hiw              1003                           Hippocampal white matter
alv                 6                          alveus of the hippocampus
vhc                38                     ventral hippocampal commissure
f                  52                                             fornix
fi                 59                         fimbria of the hippocampus
cfp              1004                              Corticofugal pathways
ic-cp-lfp-py        1              corticofugal tract and corona radiata
pyx                85                              pyramidal decussation
ml               1005                                   Medial lemniscus
ml-u               34                      medial lemniscus, unspecified
mlx                84                       medial lemniscus decussation
tht              1006                                    Thalamic tracts
eml              1051                          External medullary lamina
eml-u             249             external medullary lamina, unspecified
eml-ar            157      external medullary lamina, auditory radiation
iml               291                          internal medullary lamina
ima               290                       intramedullary thalamic area
scp-pr            270   superior cerebellar peduncle and prerubral field
ptl               239                            pretectothalamic lamina
mtg                53                            mammillotegmental tract
cst                54                       commissural stria terminalis
fr                 60                             fasciculus retroflexus
sm                 61                           stria medullaris thalami
st                 62                                   stria terminalis
hbc                80                               habenular commissure
pc                 63                               posterior commissure
7n               1007                                       Facial nerve
7n-u               35                          facial nerve, unspecified
asc7               72               ascending fibers of the facial nerve
g7                 57                           genu of the facial nerve
ofs              1008      Optic fiber system and supraoptic decussation
2n                 41                                        optic nerve
opt-och            42                       optic tract and optic chiasm
sox                83                             supraoptic decussation
tew              1009                         White matter of the tectum
csc                46              commissure of the superior colliculus
bsc                68                brachium of the superior colliculus
cic                69                    inferior colliculus, commissure
bic               146                      inferior colliculus, brachium
cbt              1010          Cerebellar and precerebellar white matter
icp                 7                       inferior cerebellar peduncle
mcp                78                         middle cerebellar peduncle
tfp                79                      transverse fibers of the pons
bsw 